### json dataset 

1. 모든 store, item에 대한 정보를 cluster별로 확보한다(이 때 3개월 단위로 합산)
2. y값에 따라 데이터를 다르게 구성한다 
3. 모델을 apply하여 예측값 산출

{1 : {'PowerCord' : [...],    
     'Shrimp' : [...],   
     'Shovel' : [...]},     
 2 : {...}  
 }

In [1]:
import pandas as pd

/opt/conda/lib/python3.8/site-packages/pandas/compat/_optional.py:161: UserWarning: Pandas requires version '2.7.1' or newer of 'numexpr' (version '2.7.0' currently installed).
  warnings.warn(msg, UserWarning)


In [ ]:
!pip install openpyxl

In [3]:
retail = pd.read_excel('../data/preprocessed/provised_retail_data.xlsx')

In [4]:
retail.head()

Unnamed: 0    Month  Store    Item_Type           Item  Sales_Total
0           0  2015-01      1  Electronics     Power Cord            0
1           1  2015-01      1  Electronics  Phone Charger            0
2           2  2015-01      1  Electronics       Ear Buds            0
3           3  2015-01      1  Electronics          Mouse            0
4           4  2015-01      1  Electronics       Keyboard            0

In [8]:
retail = retail.sort_values(by=['Month', 'Store','Item'])

In [9]:
retail.head()

Unnamed: 0    Month  Store    Item_Type      Item  Sales_Total
15          15  2015-01      1   Home Goods   Bracket            0
16          16  2015-01      1   Home Goods     Brush            0
7            7  2015-01      1      Grocery    Cereal            0
2            2  2015-01      1  Electronics  Ear Buds            0
6            6  2015-01      1      Grocery      Eggs            0

In [10]:
set(retail['Store'])

{1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,
 185

In [15]:
list(retail['Item'].value_counts().index)

['Bracket',
 'Brush',
 'Steak',
 'Shrimp',
 'Power Cord',
 'Phone Charger',
 'Paint',
 'Noodles',
 'Nails',
 'Mouse',
 'Milk',
 'King Crab',
 'Keyboard',
 'Glue',
 'Eggs',
 'Ear Buds',
 'Cereal',
 'Tape']

In [7]:
temp1 = retail[(retail['Store'] == 1) & (retail['Item'] == 'Power Cord')]

In [8]:
temp1

Unnamed: 0    Month  Store    Item_Type        Item  Sales_Total
0              0  2015-01      1  Electronics  Power Cord            0
18            18  2015-02      1  Electronics  Power Cord            0
36            36  2015-03      1  Electronics  Power Cord            0
54            54  2015-04      1  Electronics  Power Cord            0
72            72  2015-05      1  Electronics  Power Cord            0
...          ...      ...    ...          ...         ...          ...
1476        1476  2021-11      1  Electronics  Power Cord            0
1494        1494  2021-12      1  Electronics  Power Cord            0
1512        1512  2022-01      1  Electronics  Power Cord            0
1530        1530  2022-02      1  Electronics  Power Cord            0
1548        1548  2022-03      1  Electronics  Power Cord            0

[87 rows x 6 columns]

In [13]:
temp2 = temp1['Sales_Total'].tolist()

In [14]:
len(temp2)

87

In [16]:
for i in range(0,len(temp2),3):
    sum(temp2[i:i + 3])

In [19]:
def dataset_by_step(data, k):
    #k step of making data. If k = 3 -> 3 month prediction data
#     {1 : {'PowerCord' : [...],    
#      'Shrimp' : [...],   
#      'Shovel' : [...]},     
#     2 : {...}  
#     }
    dataset = dict()
    for store_id in list(sorted(retail['Store'].value_counts().index)):
        item_sales = dict()
        for item in list(retail['Item'].value_counts().index):
            store_sales = list()
            subset = data[(data['Store'] == store_id) & 
                            (data['Item'] == item)]['Sales_Total'].tolist()
            for i in range(0, len(subset), k):
                store_sales.append(sum(subset[i:i+k]))
            item_sales[item] = store_sales
        dataset[store_id] = item_sales
    return dataset

In [20]:
dataset = dataset_by_step(retail,3)

KeyboardInterrupt: 

In [32]:
dataset

{1: {'Shrimp': [0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   6,
   3,
   3,
   0,
   0],
  'Milk': [0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0],
  'Mouse': [0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   1,
   0,
   1,
   0],
  'Power Cord': [0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0],
  'Steak': [0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   4,
   2,
   0,
   0],
  'Glue': [0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0

In [35]:
import json

with open('../data/preprocessed/1_month_retail.json', 'w') as f:
    json.dump(dataset, f)